Python assignment
---

In [1]:
import numpy as np
from scipy.stats import norm

# The Black-Scholes formula

The Black–Scholes model is one of the cornerstone of mathematical finance.
The value of a European Call option for a non-dividend-paying stock $(S_t)_{t\geq 0}$ in this model is given, at time $t\in [0,T]$, by
$$
C(S_t, t, K, T) := \mathrm{e}^{-r(T-t)}\mathbb{E}\left[\max(S_{T} - K, 0)\right]
 = S_t\left(\mathcal{N}(d_{+}) - \mathrm{e}^{k}\mathcal{N}(d_{-})\right),
$$
where
$$
d_{\pm} = \frac{-k}{\sigma\sqrt{T - t}} \pm\frac{\sigma\sqrt{T-t}}{2}.
$$
Correspondingly, the price of a corresponding put option based on put–call parity is:
$$
P(S_t, t, K, T) := \mathrm{e}^{-r(T-t)}\mathbb{E}\left[\max(K-S_{T}, 0)\right]
          = S_t\left(\mathrm{e}^{k}\mathcal{N}(-d_{-}) - \mathcal{N}(-d_{+})\right).
$$
For both, as :<br>
$k := \frac{K}{S_t\mathrm{e}^{r(T - t)}}$ is called the log-forward moneyness,<br>
$\mathcal{N}(\cdot)$ is the cumulative distribution function of the standard normal distribution,<br>
$T - t$ is the time to maturity,<br>
$S_t$ is the spot price of the underlying asset,<br>
$K$ is the strike price,<br>
$r$ is the risk free rate (annual rate, expressed in terms of continuous compounding),<br>
$\sigma$ is the volatility  of returns of the underlying asset.


### Definition of the Black-Scholes class

In [6]:
class callOptionBs(object):
    ''' European call option in the Black-Scholes model.
        CP:     ## True for a Call, False for a Put
        S0:     ## Initial value of the stock price
        t0:     ## Initial time
        r:      ## instantaneous risk-free rate
        K:      ## Strike
        T:      ## Maturity (>t)
        sigma:  ## volatility parameter
Methods
=======
price : float, returns the price of the option in the Black-Scholes model
impVol: float. returns the implied volatility given an option price
'''

    def __init__(self, CP, S0, t0, r, K, T, sigma):
        self.CP = CP
        self.S0 = S0
        self.t0 = t0
        self.r = r
        self.K  = K
        self.T = T
        self.sigma = sigma
        
    def price(self):
        tau = self.T-self.t0
        sigmtau = self.sigma*np.sqrt(self.T)
        k = np.log(self.K/self.S0)  - self.r*tau
        dp = -k/sigmtau + 0.5*sigmtau
        dm = dp - sigmtau
        if self.CP: 
            return self.S0*(norm.cdf(dp) - np.exp(k)*norm.cdf(dm))
        else: 
            return self.S0*(np.exp(k)*norm.cdf(-dm) - norm.cdf(-dp))
    
    def vega(self): ## returns the Vega of the option, i.e. its derivative with respect to the volatility parameter sigma
        tau = self.T-self.t0
        sigmtau = self.sigma*np.sqrt(self.T)
        k = np.log(self.K/self.S0)  - self.r*tau
        dp = -k/sigmtau + 0.5*sigmtau
        dm = dp - sigmtau
        return self.S0 * norm.cdf(dp, 0., 1.) * np.sqrt(tau)

    def impVol(self, obsPrice, sigma0=0.2, nbIter=100):
        option = callOptionBs(self.CP, self.S0, self.t0, self.r, self.K, self.T, sigma0)
        for _ in range(nbIter):
            option.sigma -= (option.price() - obsPrice) / option.vega()
        return option.sigma

In [7]:
CP, S0, t0, K, T, r, sigma = True, 100., 0., 105., 1.0, 0.05, 0.2
option = callOptionBs(CP, S0, t0, r, K, T, sigma)
print(type(option))
print("Price = ", option.price())
print("Vega = ", option.vega())
print("Implied vol = ", option.impVol(obsPrice=7.))

<class '__main__.callOptionBs'>
Price =  8.02135223514317
Vega =  54.22283335848053
Implied vol =  0.17426990587356414


## Simulating the Black-Scholes model

We shall always consider here $t_0=0$ for simplicity.
The main idea about Monte Carlo methods is to simulate many paths of the dynamics of the process $(S_t)_{t\in [0,T]}$, to compute the payoff $\max(S_T-K, 0)$ at maturity $T$ for each simulation, and then average over all this value. One should not, eventually forget the discounting factor $e^{-rT}$. 
The Black-Scholes model in fact corresponds to continuous-time dynamics for the stock price. 
We introduce the following discretised version:<br>

$$
S_{t_{i+1}} = S_{t_i}\left(1+r \delta + \sigma\sqrt{\delta}\widetilde{n}_i\right),
$$
<br>
where $t_i = i\delta$ with $\delta:=T/N$, so that the sequence $\{t_0,t_1,\ldots,t_{N-1}\}$ represents a partition of the interval $[0,T]$ for some integer $N$.
Here, the sequence $(\widetilde{n}_0,\ldots,\widetilde{n}_{N-1})$ is an iid sequence of centered Gaussian random variables with unit variance.
Denote by $S_{t_{N}}^j = S_T^j$ the $j$-th simulation (for $j=1,\ldots,M$) of the terminal value of the stock price, according to the scheme above.


(i) Using pure Python loops (over $N$ and $M$), construct a function $\Phi_1$ giving the price of the European Call option as a function of the Black-Scholes parameters and of $M$ and $N$.<br>
(ii) Construct a similar function $\Phi_2$ avoiding (the very slow) Python loops altogether. Hint: the Numpy function np.cumsum could come in handy.<br>
(iii) Construct another function $\Phi_3$ using pandas DataFrames.<br>
(iv) For fixed $N$, say $N=100$, plot the convergence of the three functions to the exact price (given by the analytic formula above) as $M$ becomes large.<br>
(iv) Compare the performance (in terms of computation time) of the three functions $\Phi_1$, $\Phi_2$, $\Phi_3$.<br>
<br>

In all the numerical examples above, consider the following values:<br>
$$
S_0 = 100, \qquad
t_0 = 0, \qquad
K = 95, \qquad
T = 1, \qquad
r = 0, \qquad
\sigma = 15\%.
$$